In [89]:
import os
os.environ["CUDA_VISIBLE_DEVICES"]="1"
os.environ["TF_FORCE_GPU_ALLOW_GROWTH"]="true"

import tensorflow as tf
import numpy as np

import plotly
import plotly.graph_objs as go


In [40]:
N = 1000
a = 2
s = 2
o = 4
f = s

A = np.array([[1,0,1,0], [0, 1, 0, 1]])
E = np.random.randn(o, s)

SA = np.random.randn(s + a, N)

Sx = SA[:s, :]
Ax = SA[s:, :]
Sy = A @ SA

Ox = E @ Sx
Oy = E @ Sy

In [45]:
assert np.all(Sx + Ax - Sy == 0)

In [56]:
D = np.random.randn(f, o)
Ms = np.random.randn(f, f)
Ma = np.random.randn(f, a)

In [84]:
D0 = np.linalg.pinv(E)
Ms0 = A[:, :2]
Ma0 = A[:, 2:]
D, Ms, Ma = D0, Ms0, Ma0

In [66]:
Fx = D @ Ox
Fy = D @ Oy

# Adding some deltas to $D$ and $M_s$

In [100]:
deltaD1 = np.random.randn(f, o)
deltaD2 = np.random.randn(f, o)

deltaMs = np.random.randn(f, f)

In [149]:
d1r = np.linspace(-1, 1, 100) * 10
d2r = np.linspace(-1, 1, 100) * 10

In [158]:
# preparing data for the 3d plot
X, Y, Z = [], [], []


for eps1 in d1r:
    for eps2 in d2r:
        D = D0 + eps1 * deltaD1 + eps2 * deltaD2
        #Ms = Ms0 + eps2 * deltaMs

        l = Fy - Ms @ D @ Ox - Ma @ Ax
        l = np.linalg.norm(l, axis=1, ord=1)
        l = np.mean(l)
        loss = l
        
        l = R @ D @ Ox - Oy
        l = np.linalg.norm(l, axis=1, ord=1)
        l = np.mean(l)
        loss += l
        X.append(eps1)
        Y.append(eps2)
        Z.append(loss)

# Doing 3d plot

# Configure the trace.
trace1 = go.Mesh3d(x=X, y=Y, z=Z, opacity=0.5)


# Configure the layout.
layout = go.Layout(
    margin={'l': 0, 'r': 0, 'b': 0, 't': 0}
)

data = [trace1]

plot_figure = go.Figure(data=data, layout=layout)

plot_figure.update_layout(scene = dict(xaxis_title='eps1',
                    yaxis_title='eps2',
                    zaxis_title='loss',
                    #xaxis_type="log",
                    #yaxis_type="log"
                                      ),
                    width=700,
                    margin=dict(r=20, b=10, l=10, t=10))


# Render the plot.
plotly.offline.iplot(plot_figure)

In [169]:
# preparing data for the 3d plot
X, Y, Z = [], [], []


d1r = np.linspace(-1, 1, 100) * 5
d2r = np.linspace(-1, 1, 100) * 5

for eps1 in d1r:
    for eps2 in d2r:
        D = D0 + eps1 * deltaD1 #+ eps2 * deltaD2
        Ms = Ms0 + eps2 * deltaMs

        l = Fy - Ms @ D @ Ox - Ma @ Ax
        l = np.linalg.norm(l, axis=1, ord=1)
        l = np.mean(l)
        loss = l
        
        l = R @ D @ Ox - Oy
        l = np.linalg.norm(l, axis=1, ord=1)
        l = np.mean(l)
        loss += l
        X.append(eps1)
        Y.append(eps2)
        Z.append(loss)

# Doing 3d plot

# Configure the trace.
trace1 = go.Mesh3d(x=X, y=Y, z=Z, opacity=0.5)


# Configure the layout.
layout = go.Layout(
    margin={'l': 0, 'r': 0, 'b': 0, 't': 0}
)

data = [trace1]

plot_figure = go.Figure(data=data, layout=layout)

plot_figure.update_layout(scene = dict(xaxis_title='eps1',
                    yaxis_title='eps2',
                    zaxis_title='loss',
                    #xaxis_type="log",
                    #yaxis_type="log"
                                      ),
                    width=700,
                    margin=dict(r=20, b=10, l=10, t=10))


# Render the plot.
plotly.offline.iplot(plot_figure)

# Adding reconstruction loss

In [152]:
R0 = np.linalg.pinv(D)

In [153]:
deltaR = np.random.randn(o, f)
deltaD = np.random.randn(f, o)
D, Ms, Ma = D0, Ms0, Ma0

In [156]:
# preparing data for the 3d plot
X, Y, Z = [], [], []


for eps1 in d1r:
    for eps2 in d2r:
        D = D0 + eps1 * deltaD #+ eps2 * deltaD2
        Ms = Ms0 + eps2 * deltaMs
        #R = R0 + eps2 * deltaR

        l = Fy - Ms @ D @ Ox - Ma @ Ax
        l = np.linalg.norm(l, axis=1, ord=1)
        l = np.mean(l)
        loss = l
        
        l = R @ D @ Ox - Oy
        l = np.linalg.norm(l, axis=1, ord=1)
        l = np.mean(l)
        loss += l
        
        X.append(eps1)
        Y.append(eps2)
        Z.append(loss)

# Doing 3d plot

# Configure the trace.
trace1 = go.Mesh3d(x=X, y=Y, z=Z, opacity=0.5)


# Configure the layout.
layout = go.Layout(
    margin={'l': 0, 'r': 0, 'b': 0, 't': 0}
)

data = [trace1]

plot_figure = go.Figure(data=data, layout=layout)

plot_figure.update_layout(scene = dict(xaxis_title='eps1',
                    yaxis_title='eps2',
                    zaxis_title='loss',
                    #xaxis_type="log",
                    #yaxis_type="log"
                                      ),
                    width=700,
                    margin=dict(r=20, b=10, l=10, t=10))


# Render the plot.
plotly.offline.iplot(plot_figure)

# Gradients of pseudo-inverse in TensorFlow

In [133]:
# some variable
z = tf.Variable(np.array(A, dtype=np.float32))

In [134]:
# computing the gradient
with tf.GradientTape() as tape:
    z1 = tf.linalg.norm(tf.linalg.pinv(z))
tape.gradient(z1, z)

<tf.Tensor: shape=(2, 4), dtype=float32, numpy=
array([[-0.25000003,  0.        , -0.25000003,  0.        ],
       [ 0.        , -0.25000003,  0.        , -0.25000003]],
      dtype=float32)>

In [163]:
np.linalg.pinv(np.zeros((4, 4)) + 1e-10)

array([[6.25e+08, 6.25e+08, 6.25e+08, 6.25e+08],
       [6.25e+08, 6.25e+08, 6.25e+08, 6.25e+08],
       [6.25e+08, 6.25e+08, 6.25e+08, 6.25e+08],
       [6.25e+08, 6.25e+08, 6.25e+08, 6.25e+08]])